<a href="https://colab.research.google.com/github/russell-ai/topic-covid/blob/dev/tweet_topic.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# setup

In [1]:
!pip install bertopic
#!pip install bertopic --no-build-isolation --no-binary :all: # in case of conflicting with numpy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 90 kB 4.2 MB/s 
     |████████████████████████████████| 85 kB 4.8 MB/s 
     |████████████████████████████████| 88 kB 8.7 MB/s 
     |████████████████████████████████| 5.2 MB 64.4 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 662 kB 67.7 MB/s 
     |████████████████████████████████| 5.8 MB 63.3 MB/s 
     |████████████████████████████████| 1.3 MB 60.7 MB/s 
     |████████████████████████████████| 182 kB 74.5 MB/s 
     |████████████████████████████████| 7.6 MB 59.9 MB/s 
     |████████████████████████████████| 1.1 MB 62.5 MB/s 
  Created wheel for hdbscan: filename=hdbscan-0.8.29-cp38-cp38-linux_x86_64.whl size=2700846 sha256=a6f7f56d1580b4393aaea6aad6a792a5647588c410785faaae4d5179ba6330be
  Stored in directory: /root/.cache/

# load data

In [1]:
#@title Drive Downloader

from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials
import os

download_with_pydrive = True #@param {type:"boolean"}  

class Downloader(object):
    def __init__(self, use_pydrive):
        self.use_pydrive = use_pydrive

        if self.use_pydrive:
            self.authenticate()
        
    def authenticate(self):
        auth.authenticate_user()
        gauth = GoogleAuth()
        gauth.credentials = GoogleCredentials.get_application_default()
        self.drive = GoogleDrive(gauth)
    
    def download_file(self, file_id, file_dst):
        if self.use_pydrive:
            downloaded = self.drive.CreateFile({'id':file_id})
            downloaded.FetchMetadata(fetch_all=True)
            downloaded.GetContentFile(file_dst)
        else:
            !gdown --id file_dst

downloader = Downloader(download_with_pydrive)

In [2]:
current_directory = os.getcwd()
save_path = os.path.join(os.path.dirname(current_directory), "data")
os.makedirs(save_path, exist_ok=True)
model_path = os.path.join(save_path, 'sent_tweet_data.csv')

In [3]:
downloader.download_file("1k8HXp4vUBBbVqKu3kBYnu-HLDQdAdzrf", file_dst=model_path)

In [4]:
import pandas as pd

In [5]:
data = pd.read_csv("/data/sent_tweet_data.csv")
data.head()

Tweet_Id                                              Tweet  \
0  1.598104e+18  @elonmusk I thunk you're an irresponsible for ...   
1  1.598104e+18  Apparently "I've had COVID for over a week and...   
2  1.598103e+18  @snakewasright @EllenOl00313689 @iTruthSearch ...   
3  1.598103e+18  They're dropping the sequel to COVID baby wooo...   
4  1.598101e+18  @1goodtern They drop dead one by one of post C...   

                  sentiment_analysis sentiment     score  
0   ('negative', 0.8987942934036255)  negative  0.898794  
1   ('negative', 0.5844972133636475)  negative  0.584497  
2   ('negative', 0.7049756646156311)  negative  0.704976  
3    ('neutral', 0.5086733102798462)   neutral  0.508673  
4  ('negative', 0.47382649779319763)  negative  0.473826

# positive data topic analysis

In [6]:
# get the tweet text and sentiment columns whre sentiment is positive as list
positive_data = data[data["sentiment"] == "positive"]
positive_data.head()


Tweet_Id                                              Tweet  \
8   1.598098e+18  My friend spencer has covid, good thing he ate...   
16  1.598092e+18  "I had my baby shower here. Very big space, th...   
23  1.598088e+18  Nat de covid 😭✨ Se cuide, baby https://t.co/yE...   
36  1.598079e+18  Get Well Soon my baby 🥹🍼 I know you're strong ...   
75  1.598065e+18  There’s a chosen family baby I know who’s just...   

                   sentiment_analysis sentiment     score  
8   ('positive', 0.48467978835105896)  positive  0.484680  
16   ('positive', 0.9333032369613647)  positive  0.933303  
23   ('positive', 0.7633681893348694)  positive  0.763368  
36    ('positive', 0.947133481502533)  positive  0.947133  
75   ('positive', 0.5353631377220154)  positive  0.535363

In [7]:
positive_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 45263 entries, 8 to 446181
Data columns (total 5 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   Tweet_Id            45263 non-null  float64
 1   Tweet               45263 non-null  object 
 2   sentiment_analysis  45263 non-null  object 
 3   sentiment           45263 non-null  object 
 4   score               45263 non-null  float64
dtypes: float64(2), object(3)
memory usage: 2.1+ MB


## Some Tweet Cleaning

In [8]:
import re
import string
import nltk
nltk.download('stopwords')
nltk.download('wordnet')
nltk.download('punkt')
nltk.download('omw-1.4')
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import TweetTokenizer
from nltk.tokenize import word_tokenize 
from nltk.corpus import stopwords

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package omw-1.4 to /root/nltk_data...


In [9]:
URL_REGEX = re.compile('http(s)?:\/\/t.co\/\w+')
MENTION_REGEX = re.compile('@\w+')

def clean_tweet(tweet):
    # remove mentions, the pound sign, and replace urls with URL token
    tweet = re.sub(URL_REGEX, '', tweet)
    tweet = re.sub(MENTION_REGEX, '', tweet)
    tweet = tweet.replace('#', '')
    tweet = re.sub(r'\d+', '', tweet)
    return tweet.strip()

def remove_stopwords(text):
    removed = []
    stop_words = list(stopwords.words("english"))
    tokens = word_tokenize(text)
    for i in range(len(tokens)):
        if tokens[i] not in stop_words:
            removed.append(tokens[i])
    return " ".join(removed)


def lemmatizing(text):
    lemmatizer = WordNetLemmatizer()
    tokens = word_tokenize(text)
    for i in range(len(tokens)):
        lemma_word = lemmatizer.lemmatize(tokens[i])
        tokens[i] = lemma_word
    return " ".join(tokens)


def remove_punctuation(text):
    return text.translate(str.maketrans('', '', string.punctuation))


def remove_emojis(text):
    wierd_pattern = re.compile("["
        u"\U0001F600-\U0001F64F"  # emoticons
        u"\U0001F300-\U0001F5FF"  # symbols & pictographs
        u"\U0001F680-\U0001F6FF"  # transport & map symbols
        u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
        u"\U00002702-\U000027B0"
        u"\U000024C2-\U0001F251"
        u"\U0001f926-\U0001f937"
        u'\U00010000-\U0010ffff'
        u"\u200d"
        u"\u2640-\u2642"
        u"\u2600-\u2B55"
        u"\u23cf"
        u"\u23e9"
        u"\u231a"
        u"\u3030"
        u"\ufe0f"
        u"\u2069"
        u"\u2066"
        # u"\u200c"
        u"\u2068"
        u"\u2067"
        "]+", flags=re.UNICODE)
    
    return wierd_pattern.sub(r'', text)

In [10]:
def tweet_cleaner(tweet):
    tweet = clean_tweet(tweet)
    tweet = remove_emojis(tweet)
    tweet = remove_punctuation(tweet)
    tweet = remove_stopwords(tweet)
    tweet = lemmatizing(tweet)
    return tweet

In [11]:
positive_data["cleaned_tweet"] = positive_data["Tweet"].apply(lambda s: tweet_cleaner(s))

<ipython-input-11-a7f4dd509c12>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  positive_data["cleaned_tweet"] = positive_data["Tweet"].apply(lambda s: tweet_cleaner(s))


In [12]:
positive_data.head()

Tweet_Id                                              Tweet  \
8   1.598098e+18  My friend spencer has covid, good thing he ate...   
16  1.598092e+18  "I had my baby shower here. Very big space, th...   
23  1.598088e+18  Nat de covid 😭✨ Se cuide, baby https://t.co/yE...   
36  1.598079e+18  Get Well Soon my baby 🥹🍼 I know you're strong ...   
75  1.598065e+18  There’s a chosen family baby I know who’s just...   

                   sentiment_analysis sentiment     score  \
8   ('positive', 0.48467978835105896)  positive  0.484680   
16   ('positive', 0.9333032369613647)  positive  0.933303   
23   ('positive', 0.7633681893348694)  positive  0.763368   
36    ('positive', 0.947133481502533)  positive  0.947133   
75   ('positive', 0.5353631377220154)  positive  0.535363   

                                        cleaned_tweet  
8   My friend spencer covid good thing ate pound e...  
16  I baby shower Very big space owner accommodati...  
23                         Nat de covid Se cuide baby  
36  Get Well Soon baby I know youre strong COVID w...  
75  There ’ chosen family baby I know ’ cuddliest ...

In [13]:
positive_tweets = positive_data["cleaned_tweet"].tolist()

In [14]:
len(positive_tweets)

45263

## topic modelling

In [15]:
from bertopic import BERTopic

[Topic Model Spesifications:](https://www.sbert.net/docs/pretrained_models.html#other-models) 

In [16]:
topic_model = BERTopic(verbose=True, embedding_model="all-mpnet-base-v2", min_topic_size=50,  calculate_probabilities=False)

In [17]:
topics, probs = topic_model.fit_transform(positive_tweets)

Downloading:   0%|          | 0.00/1.18k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/190 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/10.6k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/571 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/116 [00:00<?, ?B/s]

...

Downloading:   0%|          | 0.00/13.1k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/232k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/349 [00:00<?, ?B/s]

Batches:   0%|          | 0/1415 [00:00<?, ?it/s]

2022-12-22 10:22:28,319 - BERTopic - Transformed documents to Embeddings
2022-12-22 10:24:00,064 - BERTopic - Reduced dimensionality
2022-12-22 10:24:06,362 - BERTopic - Clustered reduced embeddings


In [18]:
freq = topic_model.get_topic_info()

In [19]:
freq.head(20)

Topic  Count                                       Name
0      -1  23384                    -1_covid_baby_birth_amp
1       0   4547  0_vaccine_vaccinated_vaccination_pregnant
2       1   1667         1_test_negative_pregnancy_positive
3       2   1361                2_birthday_happy_month_year
4       3   1112        3_pregnant_pregnancy_congrats_covid
5       4    658            4_biden_trump_formula_president
6       5    646                  5_coma_story_miracle_twin
7       6    626               6_anniversary_india_birth_th
8       7    618         7_pregnancy_study_research_article
9       8    583                       8_help_would_job_due
10      9    577                   9_back_baby_stream_covid
11     10    529   10_breastfeeding_vaccine_milk_breastfeed
12     11    440               11_negative_test_tested_came
13     12    428                    12_soon_well_better_get
14     13    341               13_meet_friend_sister_cousin
15     14    311                  14_mask_wearing_wear_face
16     15    268        15_christmas_jesus_christ_celebrate
17     16    251               16_concert_tour_music_ticket
18     17    237   17_positive_hospital_mother_successfully
19     18    226       18_florence_nurses_nightingale_nurse

In [20]:
topic_model.get_topic(0)  # Select the most frequent topic

[('vaccine', 0.03482831042529213),
 ('vaccinated', 0.021422517455755002),
 ('vaccination', 0.020661122901810113),
 ('pregnant', 0.017644982966336643),
 ('pregnancy', 0.017154575439040278),
 ('safe', 0.015827943596731377),
 ('shot', 0.015125219972060204),
 ('get', 0.014101877885987732),
 ('woman', 0.01373839492662166),
 ('booster', 0.013682459716682934)]

In [21]:
topic_model.get_topic(1)

[('test', 0.12846939479451852),
 ('negative', 0.05469349855100696),
 ('pregnancy', 0.03929453113725697),
 ('positive', 0.038428954448921415),
 ('result', 0.022782048410156134),
 ('like', 0.018544420192664623),
 ('testing', 0.0176423956231016),
 ('rapid', 0.016810802252041356),
 ('thought', 0.01641713690674787),
 ('tested', 0.015200657028669986)]

In [22]:
topic_model.get_topic(2)

[('birthday', 0.05690233562911928),
 ('happy', 0.028758058617471646),
 ('month', 0.01926086610371855),
 ('year', 0.01906604166696804),
 ('shower', 0.01874391189365614),
 ('party', 0.01808926194534138),
 ('day', 0.01653996404479526),
 ('birth', 0.01576945919268044),
 ('bday', 0.01278502953920831),
 ('covid', 0.010850999429852284)]

## Topic Visualization

In [23]:
topic_model.visualize_topics()

In [24]:
topic_model.visualize_barchart()

In [25]:
topic_model.visualize_heatmap()

In [26]:
topic_model.visualize_term_rank()

In [27]:
topic_model.visualize_hierarchy()

# neutral topic analysis

In [28]:
# get the tweet text and sentiment columns whre sentiment is positive as list
neutral_data = data[data["sentiment"] == "neutral"]
neutral_data.head()


Tweet_Id                                              Tweet  \
3   1.598103e+18  They're dropping the sequel to COVID baby wooo...   
15  1.598093e+18                                    Baby 🦁\nCovid 👽   
19  1.598090e+18  @DiedSuddenly_ In the 1950s I had polio. Spent...   
27  1.598086e+18  Brianna has informed us that $0/$600 has been ...   
29  1.598084e+18  @eternity_comics Is a baby gonna debate me? Is...   

                 sentiment_analysis sentiment     score  
3   ('neutral', 0.5086733102798462)   neutral  0.508673  
15  ('neutral', 0.7114819288253784)   neutral  0.711482  
19  ('neutral', 0.6331275701522827)   neutral  0.633128  
27  ('neutral', 0.7449110150337219)   neutral  0.744911  
29  ('neutral', 0.5940708518028259)   neutral  0.594071

In [29]:
neutral_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 160298 entries, 3 to 446215
Data columns (total 5 columns):
 #   Column              Non-Null Count   Dtype  
---  ------              --------------   -----  
 0   Tweet_Id            160298 non-null  float64
 1   Tweet               160298 non-null  object 
 2   sentiment_analysis  160298 non-null  object 
 3   sentiment           160298 non-null  object 
 4   score               160298 non-null  float64
dtypes: float64(2), object(3)
memory usage: 7.3+ MB


## Some Tweet Cleaning

In [30]:
neutral_data["cleaned_tweet"] = neutral_data["Tweet"].apply(lambda s: tweet_cleaner(s))

In [31]:
neutral_data.head()

Tweet_Id                                              Tweet  \
3   1.598103e+18  They're dropping the sequel to COVID baby wooo...   
15  1.598093e+18                                    Baby 🦁\nCovid 👽   
19  1.598090e+18  @DiedSuddenly_ In the 1950s I had polio. Spent...   
27  1.598086e+18  Brianna has informed us that $0/$600 has been ...   
29  1.598084e+18  @eternity_comics Is a baby gonna debate me? Is...   

                 sentiment_analysis sentiment     score  \
3   ('neutral', 0.5086733102798462)   neutral  0.508673   
15  ('neutral', 0.7114819288253784)   neutral  0.711482   
19  ('neutral', 0.6331275701522827)   neutral  0.633128   
27  ('neutral', 0.7449110150337219)   neutral  0.744911   
29  ('neutral', 0.5940708518028259)   neutral  0.594071   

                                        cleaned_tweet  
3         Theyre dropping sequel COVID baby woooooooo  
15                                         Baby Covid  
19  In I polio Spent summer bed Id first new Salk ...  
27  Brianna informed u raised today baby tested po...  
29    Is baby gon na debate Is mock trial baby lawyer

In [32]:
neutral_data = neutral_data["cleaned_tweet"].tolist()

In [33]:
len(neutral_data)

160298

## topic modelling

In [34]:
topic_model = BERTopic(verbose=True, embedding_model="all-mpnet-base-v2", min_topic_size=50,  calculate_probabilities=False)

In [35]:
topics, probs = topic_model.fit_transform(neutral_data)

Batches:   0%|          | 0/5010 [00:00<?, ?it/s]

2022-12-22 10:41:55,220 - BERTopic - Transformed documents to Embeddings
2022-12-22 10:52:56,466 - BERTopic - Reduced dimensionality
2022-12-22 10:53:25,081 - BERTopic - Clustered reduced embeddings


In [37]:
freq = topic_model.get_topic_info()

In [38]:
freq.head(20)

Topic  Count                                          Name
0      -1  82494                  -1_pregnant_woman_covid_baby
1       0   7429                     0_test_negative_rapid_kit
2       1   3220                 1_rate_boom_expectancy_boomer
3       2   3189                2_shot_vaccinated_vaxxed_polio
4       3   3108              3_certificate_date_passport_name
5       4   2628                 4_abortion_biden_trump_choice
6       5   1891                   5_petition_nhs_sign_partner
7       6   1492  6_breastfeeding_lactating_recommended_trying
8       7   1341                      7_mask_wear_wearing_wore
9       8   1061               8_control_pill_effective_condom
10      9   1054                  9_data_safety_evidence_trial
11     10   1010       10_breastfeeding_milk_breastfeed_breast
12     11    946                 11_black_bame_ethnic_minority
13     12    841      12_fertility_affect_infertility_evidence
14     13    793                 13_parliament_being_stop_from
15     14    740        14_sarscov_infection_maternal_neonatal
16     15    739                    15_clot_blood_control_pill
17     16    731           16_mental_anxiety_depression_stress
18     17    711                        17_job_help_work_money
19     18    656               18_tier_pandemic_business_world

In [39]:
topic_model.get_topic(0)  # Select the most frequent topic

[('test', 0.03937590513793042),
 ('negative', 0.014003454786522792),
 ('rapid', 0.011726330108577238),
 ('kit', 0.01154664936518822),
 ('result', 0.011282326205169396),
 ('testing', 0.01113251140674331),
 ('like', 0.01097076852312988),
 ('positive', 0.010856289353362896),
 ('line', 0.00934032856700938),
 ('thought', 0.008597814823533171)]

In [40]:
topic_model.get_topic(1)

[('rate', 0.03104853687760367),
 ('boom', 0.020969183115817313),
 ('expectancy', 0.020670730140590638),
 ('boomer', 0.01363660610017227),
 ('population', 0.01173844555926125),
 ('death', 0.011164250045713623),
 ('decline', 0.011144222666257317),
 ('year', 0.010039930148292336),
 ('life', 0.009532309311866768),
 ('average', 0.009295386010420782)]

In [41]:
topic_model.get_topic(2)

[('shot', 0.010879646647879423),
 ('vaccinated', 0.009188150511618833),
 ('vaxxed', 0.008893057470509974),
 ('polio', 0.008557895317578564),
 ('vaccine', 0.008366477956845699),
 ('got', 0.008104197229146732),
 ('kid', 0.007101578586950225),
 ('toddler', 0.006991920307458353),
 ('my', 0.006374168336887527),
 ('old', 0.00590857441557219)]

## Topic Visualization

In [42]:
topic_model.visualize_topics()

In [43]:
topic_model.visualize_barchart()

In [44]:
topic_model.visualize_heatmap()

In [45]:
topic_model.visualize_term_rank()

In [46]:
topic_model.visualize_hierarchy()

# negative topic analysis

In [36]:
# get the tweet text and sentiment columns whre sentiment is positive as list
negative_tweet_data = data[data["sentiment"] == "negative"]
negative_tweet_data.head()


Tweet_Id                                              Tweet  \
0  1.598104e+18  @elonmusk I thunk you're an irresponsible for ...   
1  1.598104e+18  Apparently "I've had COVID for over a week and...   
2  1.598103e+18  @snakewasright @EllenOl00313689 @iTruthSearch ...   
4  1.598101e+18  @1goodtern They drop dead one by one of post C...   
5  1.598101e+18  @DesertCamel77 @Kate_DowlingNZ But they are ta...   

                  sentiment_analysis sentiment     score  
0   ('negative', 0.8987942934036255)  negative  0.898794  
1   ('negative', 0.5844972133636475)  negative  0.584497  
2   ('negative', 0.7049756646156311)  negative  0.704976  
4  ('negative', 0.47382649779319763)  negative  0.473826  
5    ('negative', 0.811675488948822)  negative  0.811675

In [47]:
negative_tweet_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 240654 entries, 0 to 446209
Data columns (total 5 columns):
 #   Column              Non-Null Count   Dtype  
---  ------              --------------   -----  
 0   Tweet_Id            240654 non-null  float64
 1   Tweet               240654 non-null  object 
 2   sentiment_analysis  240654 non-null  object 
 3   sentiment           240654 non-null  object 
 4   score               240654 non-null  float64
dtypes: float64(2), object(3)
memory usage: 11.0+ MB


## Some Tweet Cleaning

In [48]:
negative_tweet_data["cleaned_tweet"] = negative_tweet_data["Tweet"].apply(lambda s: tweet_cleaner(s))

In [49]:
negative_tweet_data.head()

Tweet_Id                                              Tweet  \
0  1.598104e+18  @elonmusk I thunk you're an irresponsible for ...   
1  1.598104e+18  Apparently "I've had COVID for over a week and...   
2  1.598103e+18  @snakewasright @EllenOl00313689 @iTruthSearch ...   
4  1.598101e+18  @1goodtern They drop dead one by one of post C...   
5  1.598101e+18  @DesertCamel77 @Kate_DowlingNZ But they are ta...   

                  sentiment_analysis sentiment     score  \
0   ('negative', 0.8987942934036255)  negative  0.898794   
1   ('negative', 0.5844972133636475)  negative  0.584497   
2   ('negative', 0.7049756646156311)  negative  0.704976   
4  ('negative', 0.47382649779319763)  negative  0.473826   
5    ('negative', 0.811675488948822)  negative  0.811675   

                                       cleaned_tweet  
0  I thunk youre irresponsible allowing antivaxxe...  
1  Apparently Ive COVID week Im immunocompromised...  
2  Yeah ’ easier believe Democrats eat pizza baby...  
4  They drop dead one one post COVID cardiac issu...  
5  But taking baby unmasked crowded area covid in...

In [50]:
negative_tweet_data = negative_tweet_data["cleaned_tweet"].tolist()

In [51]:
len(negative_tweet_data)

240654

## topic modelling

In [52]:
topic_model = BERTopic(verbose=True, embedding_model="all-mpnet-base-v2", min_topic_size=50,  calculate_probabilities=False)

In [53]:
topics, probs = topic_model.fit_transform(negative_tweet_data)

Batches:   0%|          | 0/7521 [00:00<?, ?it/s]

2022-12-22 11:06:34,597 - BERTopic - Transformed documents to Embeddings
2022-12-22 11:25:39,750 - BERTopic - Reduced dimensionality
2022-12-22 11:26:28,051 - BERTopic - Clustered reduced embeddings


In [54]:
freq = topic_model.get_topic_info()

In [55]:
freq.head(20)

Topic   Count                                          Name
0      -1  136414                    -1_baby_covid_pregnant_amp
1       0   11251             0_test_testing_pregnancy_negative
2       1    4649                     1_mask_wear_wearing_masks
3       2    4481                 2_abortion_pro_choice_prolife
4       3    4191  3_vaccine_vaccinated_vaccination_miscarriage
5       4    3851               4_preterm_risk_severe_increased
6       5    2952                           5_job_help_work_due
7       6    2605            6_hospital_partner_patient_allowed
8       7    2321                      7_vaccine_jab_polio_shot
9       8    2317        8_republicans_gop_democrats_republican
10      9    2017              9_certificate_date_passport_name
11     10    1875                   10_control_pill_side_effect
12     11    1676                  11_boris_brexit_johnson_tory
13     12    1527                 12_china_chinese_wuhan_chinas
14     13    1525                    13_clot_blood_control_pill
15     14    1376                14_trump_president_he_election
16     15    1300       15_contagious_isnt_difference_pregnancy
17     16    1147               16_black_white_racism_disparity
18     17    1126               17_teacher_school_student_class
19     18    1055                          18_fuck_baby_oh_suck

In [56]:
topic_model.get_topic(0)  # Select the most frequent topic

[('test', 0.043519642875595274),
 ('testing', 0.014681640959839135),
 ('pregnancy', 0.014413959131715368),
 ('negative', 0.012843262529869897),
 ('positive', 0.011985794293211388),
 ('result', 0.011309192932343504),
 ('waiting', 0.009315592646243577),
 ('rapid', 0.008719607674441503),
 ('like', 0.008392568053598665),
 ('look', 0.007638435800164863)]

In [57]:
topic_model.get_topic(1)

[('mask', 0.04176114299550817),
 ('wear', 0.025648336697172546),
 ('wearing', 0.020591681589448567),
 ('masks', 0.00604090860831915),
 ('masked', 0.005474248221971408),
 ('masking', 0.005444516331229531),
 ('face', 0.005291848172773664),
 ('wore', 0.004644837663483384),
 ('unmasked', 0.004063583407518191),
 ('around', 0.004050630658075676)]

In [58]:
topic_model.get_topic(2)

[('abortion', 0.022670914515475968),
 ('pro', 0.01781130692468876),
 ('choice', 0.015678148895774836),
 ('prolife', 0.014981939972516541),
 ('body', 0.012660551840794966),
 ('life', 0.011098678370168261),
 ('forced', 0.007914948178052389),
 ('autonomy', 0.00737788525355125),
 ('right', 0.007106304731564585),
 ('kill', 0.0064060797522279295)]

## Topic Visualization

In [59]:
topic_model.visualize_topics()

In [60]:
topic_model.visualize_barchart()

In [65]:
topic_model.visualize_heatmap(top_n_topics=25)

In [62]:
topic_model.visualize_term_rank()

In [63]:
topic_model.visualize_hierarchy()

## Save/Load BERTopic model

In [66]:
topic_model.save("negative_model")

/usr/local/lib/python3.8/dist-packages/scipy/sparse/_index.py:125: SparseEfficiencyWarning:

Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.



In [ ]:
topic_model = BERTopic.load("negative_model")


`russell-ai`

